# Project 2: Linear Regression – California Wildfires
The goal of this project is to predict acres burned given a California wildfire by using linear regression to identify relationships between acres burned and weather & time.

# Libraries and Options

## Import Libraries

In [1]:
import requests
import re
import pandas as pd
import pickle
import datetime
import numpy as np

# quick data analysis
from pandas_profiling import ProfileReport

# visualizations
import matplotlib.pyplot as plt
import plotly.graph_objects as go
import plotly.express as px
import plotly.io as pio
pio.renderers.default = "notebook"

## Configure Options & Settings at Interpreter Startup

In [2]:
def start():
    options = {
        'display': {
            'max_columns': None,
            'max_colwidth': 100,
            'expand_frame_repr': False,  # Don't wrap to multiple pages
            'max_rows': 25,
            'max_seq_items': 25,         # Max length of printed sequence
            'precision': 5,
            'show_dimensions': False
        },
        'mode': {
            'chained_assignment': None   # Controls SettingWithCopyWarning
        }
    }

    for category, option in options.items():
        for op, value in option.items():
            pd.set_option(f'{category}.{op}', value)  # Python 3.6+

if __name__ == '__main__':
    start()
    del start  # Clean up namespace in the interpreter

# Request data from www.fire.ca.gov

## Get text from each incidents page for the past 7 years
The data retrieved from <www.fire.ca.gov> contains a block of javascript text with a table of incident data.   
The script below pulls only the incidents table for each year.

In [5]:
year = ['2019', '2018', '2017', '2016', '2015', '2014', '2013']
domain = 'https://www.fire.ca.gov/incidents/'
links = [domain + y for y in year]
pages = ''
string_to_find = "incidentListTableInitialData ="
for url in links:
    response = requests.get(url)
    print(f'{url}', response.status_code) # untested
    page = response.text
    start_position = page.find(string_to_find)
    pages += response.text[start_position:]

https://www.fire.ca.gov/incidents/2019 200
https://www.fire.ca.gov/incidents/2018 200
https://www.fire.ca.gov/incidents/2017 200
https://www.fire.ca.gov/incidents/2016 200
https://www.fire.ca.gov/incidents/2015 200
https://www.fire.ca.gov/incidents/2014 200
https://www.fire.ca.gov/incidents/2013 200


# Create wildfire data frame

We'll be storing the data in a dictionary and then creating a dataframe. First we have to:
1. Change null values to "null"
2. Change true values to "true"
3. Change false values to "false"
4. Create dictionary from the data
5. Create dataframe from the dictionary with keys as columns & values as rows

I later learned that I could have used 'response.json' instead of '.text' which would have done this in one step 😳

## Pickle 'pages'

In [6]:
# with open('data/initial_import.pickle', 'wb') as to_write:
#     pickle.dump(pages, to_write)

In [4]:
# with open('data/initial_import.pickle', 'rb') as read_file:
#     pages = pickle.load(read_file)

## Replace true, false, and null to strings  

In [8]:
replace_true = (re.sub('true', "\"true\"", pages))
replace_false = (re.sub('false', "\"false\"", replace_true))
replace_null_and_bool = (re.sub('null', "\"null\"" , replace_false))
cleaned_dicts = replace_null_and_bool
type(cleaned_dicts)

str

## Extract target data with regex

In [9]:
yearly_incidents_list = re.findall(r'Data\s\=\s\[(\{.+\})];', cleaned_dicts) # 'result' type is a list
# type(yearly_incidents_list)

## Create a tuple of dicts by year

In [10]:
tuple_of_dictionaries = ()
for string_dict in yearly_incidents_list:
    tuple_of_dictionaries += eval(string_dict)
# type(tuple_of_dictionaries)

## Create pandas dataframe from tuple of dicts

In [11]:
df = pd.DataFrame(tuple_of_dictionaries)

# Data Cleaning: Clean wildfire data frame

## Pickle our first data frame
This serves as a good checkpoint given part 1 of the data cleaning is complete

In [ ]:
# df.to_pickle('data/original_wildfire_df.pickle')

In [12]:
# df = pd.read_pickle('data/original_wildfire_df.pickle')

## Strip column names

In [13]:
df.columns = df.columns.str.strip()

## Strip 'Name' column

In [14]:
df['Name'] = df['Name'].str.strip()

## Remove unnecessary columns

In [15]:
# Consider keeping 'CalFireIncident' as they might have better record-keeping
columns_to_remove = [
    'FuelType', 'PercentContained', 'ControlStatement', 'ConditionStatement',
    'SearchDescription', 'SearchKeywords', 'AdminUnit', 'Updated',
    'ArchiveYear', 'Public', 'Active', 'Featured', 'Final',
    'Status', 'CanonicalUrl', 'StructuresDestroyed', 'StructuresDamaged',
    'StructuresThreatened', 'StructuresEvacuated', 'PersonnelInvolved',
    'CrewsInvolved', 'Injuries', 'Fatalities', 'Helicopters', 'Engines',
    'Dozers', 'WaterTenders', 'AirTankers'
]
df = df.drop(columns_to_remove, axis=1)

## Change 'true/false' from string to boolean

In [16]:
df['MajorIncident'] = df['MajorIncident'].map(dict(true=1, false=0))

## Change "null" to NaN

In [17]:
df = df.replace('null', np.NaN)

In [18]:
df.isna().sum()

UniqueId            0
Name                0
Location            0
Latitude            0
Longitude           0
AcresBurned         3
Counties            0
CountyIds           0
Started             0
Extinguished       59
CalFireIncident     0
MajorIncident       0
dtype: int64

## Drop rows with NaN values

In [19]:
df.dropna(subset=['AcresBurned', 'Extinguished'], how='any', inplace=True)

## Drop rows with 0.0 lat/lng

In [20]:
lat_zero = df[df['Latitude'] == 0.0].index
df.drop(lat_zero, inplace=True)

## Create 'DateTime' column
Format needs to be [YYYY]-[MM]-[DD]T[HH]:[MM]:[SS][timezone] for the Dark Sky API request

In [21]:
df['DateTime'] = df['Started'].str.extract('(\d{4}-\d{2}-\d\dT\d\d:\d\d:\d\d)') + 'Z'

In [22]:
# df['Started'] = df['Started'].str.replace('(T[\d:\.]+Z)', 'T20:00:00Z', regex=True) # Replace time

## Convert date strings to datetime objects

In [23]:
df['Started'] = pd.to_datetime(df['Started'])
df['Extinguished'] = pd.to_datetime(df['Extinguished'])

## Create 'Duration' column

In [24]:
df['DurationDays'] = (df['Extinguished'] - df['Started']).dt.days + 1 # adding 1 to be inclusive

## [Skip] Let's take a closer look at 'duration'
Issues here may indicate an issue with the 'Extinguished' date

In [26]:
# fig = px.histogram(df, x='DurationDays',
#                    title='Histogram of Wildfire Duration',
#                    labels={'DurationDays':'Duration (days)'}, # can specify one label per df column
#                    opacity=0.8,
#                    log_y=True, # represent bars with log scale
#                    color_discrete_sequence=['indianred'] # color of histogram bars
#                    )
# fig.show()

In [25]:
# df['DurationDays'].describe()

## Remove rows where the 'Extinguished' date is after the 'Started' date

In [26]:
df.drop(df.loc[df['DurationDays'] < 1].index, inplace=True)

## Remove rows with 'Started' and 'Extinguished' dates before minimum date of import data

In [27]:
date_filter = '2013-01-01' # Minimum date of import data, any date before this is erroneous
df.drop(df.loc[(df['Started'] < date_filter) | (df['Extinguished'] < date_filter)].index, inplace=True)

## Sort by 'Started' and reset the index

In [30]:
df = df.sort_values(by='Started', ascending=False).reset_index()

## [Skip] Consider removing rows with 'DurationDays' > 90 days
The biggest fires don't seem to last more than 2 months

## [Skip] Replace null 'Extinguished' dates with "inferred" date

This was canceled as the variation of acres burned and duration is too high to accurately infer.

After finding the median duration of a wildfire, we can add it to date the wildfire started to infer the extinguished date.

### Median duration of wildfire

In [ ]:
# Create a dataframe without null 'Extinguished' dates
non_null_df = df[df['Extinguished'].notna()]
# Convert them to a datetme
non_null_df['Extinguished'] = pd.to_datetime(df['Extinguished'])
# Get the timedelta
non_null_df['Duration'] = non_null_df['Extinguished'] - non_null_df['Started']
# Convert timedelta to int and assign it to a variable
median_duration = non_null_df['Duration'].dt.days.median()

### Median Acres burned

In [ ]:
median_acres_burned = df['AcresBurned'].median()

In [ ]:
median_acres_burned_daily = median_acres_burned / median_duration

In [ ]:
test = df[(df['Extinguished'].isna()) & (df['AcresBurned'] > 0)]
test

#### Median duration of wildfire

In [ ]:
# Create a dataframe without null 'Extinguished' dates
non_null_df = df[df['Extinguished'].notna()]
# Convert them to a datetme
non_null_df['Extinguished'] = pd.to_datetime(df['Extinguished'])
# Get the timedelta
non_null_df['Duration'] = non_null_df['Extinguished'] - non_null_df['Started']
# Convert timedelta to int and assign it to a variable
median_duration = non_null_df['Duration'].dt.days.median()

#### Median Acres burned

In [ ]:
median_acres_burned = df['AcresBurned'].median()

In [ ]:
median_acres_burned_daily = median_acres_burned / median_duration

#### If a row has 'AcresBurned', we can infer the duration of the wildfire

In [ ]:
test['log_acres_burned'] = np.log(test['AcresBurned'])

In [ ]:
acres_burned = df['AcresBurned'] / median_duration
test['DurationInferred'] = (test['AcresBurned'] / median_acres_burned_daily).round()
test

In [ ]:
# df[(df['Extinguished'].isna()) & (df['AcresBurned'] > 0)].shape

#### Add 'median_duration' to 'Started' date to get the 'Extinguished' date

In [ ]:
# df['Started'] + datetime.timedelta(days=median_duration)

### Replace 'Extinguished' date as there are rows that have both 'AcresBurned' == 0 and 'Extinguished' is NaN

In [ ]:
df[((df['AcresBurned'] == 0) | (df['AcresBurned'].isna())) & (df['Extinguished'].isna())]

## [Skip] Replacing NaN/0 values with the median (AcresBurned)

In [ ]:
df[(df['AcresBurned'] == 0) | (df['AcresBurned'].isna())]

#### Get the median acres burned per day

In [ ]:
# df.loc[df['AcresBurned'] > 0, ['AcresBurned']].plot(kind='hist', bins=100)

#### Infer acres burned for rows with NaN/0 acres burned
We can multiply the 'duration' of the fire with the median acres burned per day

In [ ]:
# null_acres_burned = df[df['AcresBurned'].isna()] # .shape[0]
df[(df['AcresBurned'] == 0) | (df['AcresBurned'].isna())].replace(
    to_replace=[np.nan, 0], value=median_acres_burned)

## [BONUS] Validate dataframe
Let's crosscheck a few rows with the data in <www.fire.ca.gov>.  

## Run Profile Report of Wildfire data frame
This is to check for any additional data cleaning that might be necessary

In [ ]:
profile = ProfileReport(df, title='Pandas Profiling Report', html={'style':{'full_width':True}})
profile.to_notebook_iframe()

![title](img/validate_wildfires.png)

# Request weather data from the Dark Sky API

## Pickle cleaned data frame

In [ ]:
# df.to_pickle('data/part2_cleaned_df.pickle')

In [28]:
# df = pd.read_pickle('data/part2_cleaned_df.pickle')

## Create new column with all url parameters

In [31]:
url_start = 'https://api.darksky.net/forecast/4f4ef1267ba7015a5e1b8aee6fb45ded/'
url_end = '?exclude=currently,minutely,hourly,flags.json'
df['WeatherDirectory'] = url_start + df['Latitude'].astype(
    str) + ',' + df['Longitude'].astype(str) + ',' + df['DateTime'].astype(str) + url_end

## Flatten json function

In [32]:
def flatten_json(y):
    out = {}

    def flatten(x, name=''):
        if type(x) is dict:
            for a in x:
                flatten(x[a], name + a + '_')
        elif type(x) is list:
            i = 0
            for a in x:
                flatten(a, name + str(i) + '_')
                i += 1
        else:
            out[name[:-1]] = x

    flatten(y)
    return out

## Import weather data and create weather data frame
The Dark Sky API requires the url to have the latitude, longitude, and timestamp.  
The code below makes a call for each start date of a wildfire (1 row per wildfire) and appends the weather data to a dataframe as a row.  
It also includes a 'unique_id' to use as a key in merging data frames.

In [33]:
weather_df = pd.DataFrame()
new_unique_id = []

for index, row in df.iterrows():
    response = requests.get(row['WeatherDirectory']) # timeout=0.001
#     print(f'{link}', response.status_code) # 200 success
#     if response.status_code == 200:
    dark_sky_json = response.json()
    flat = flatten_json(dark_sky_json)
    weather_df = weather_df.append(flat, ignore_index=True)
    new_unique_id.append(row['UniqueId'])
#     weather_df['unique_id'] = batch_1['UniqueId']
weather_df['uniqueid'] = new_unique_id

## [Canceled ] Dark Sky Python API
I emailed the owner of this API and there was an error in the 'readme' file which is why the script below didn't work.  
I came up with an alternate solution as seen above.

In [ ]:
# # Canceled
# from darksky.api import DarkSky, DarkSkyAsync
# from darksky.types import languages, units, weather
# from datetime import datetime as dt

# API_KEY = '4f4ef1267ba7015a5e1b8aee6fb45ded'

# darksky = DarkSky(API_KEY)
# t = dt(2018, 5, 6, 12)

# latitude = 42.3601
# longitude = -71.0589
# forecast = darksky.get_forecast(
#     latitude, longitude,
#     extend=False, # default `False`
#     lang=languages.ENGLISH, # default `ENGLISH`
#     units=units.AUTO, # default `auto`
#     exclude=[weather.MINUTELY, weather.ALERTS], # default `[]`,
#     timezone='UTC' # default None - will be set by DarkSky API automatically
# )

# # Final wrapper identical for both ways
# forecast.latitude # 42.3601
# forecast.longitude # -71.0589
# forecast.timezone # timezone for coordinates. For exmaple: `America/New_York`

# forecast.currently # CurrentlyForecast. Can be found at darksky/forecast.py
# forecast.minutely # MinutelyForecast. Can be found at darksky/forecast.py
# forecast.hourly # HourlyForecast. Can be found at darksky/forecast.py
# forecast.daily # DailyForecast. Can be found at darksky/forecast.py
# forecast.alerts # [Alert]. Can be found at darksky/forecast.py

# Data Cleaning: Clean weather data frame

## Pickle our first weather data frame

In [124]:
# weather_df.to_pickle('data/weather_first_df.pickle')

In [34]:
# weather_df = pd.read_pickle('data/weather_first_df.pickle')

## Create CSV files
Create CSV to do some sanity checks

In [35]:
# weather_df.to_csv(
#     '/Users/miguel/Git_Repos/sf20_ds17/corralm_projects/Project 2 – California Wildfires/weather_df_1.csv'
# )

## Remove unnecessary columns

Many of the features are essentially the same. We can remove these or feature engineer them.

In [36]:
weather_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1376 entries, 0 to 1375
Data columns (total 45 columns):
daily_data_0_apparentTemperatureHigh        1373 non-null float64
daily_data_0_apparentTemperatureHighTime    1373 non-null float64
daily_data_0_apparentTemperatureLow         1371 non-null float64
daily_data_0_apparentTemperatureLowTime     1371 non-null float64
daily_data_0_apparentTemperatureMax         1373 non-null float64
daily_data_0_apparentTemperatureMaxTime     1373 non-null float64
daily_data_0_apparentTemperatureMin         1373 non-null float64
daily_data_0_apparentTemperatureMinTime     1373 non-null float64
daily_data_0_cloudCover                     1234 non-null float64
daily_data_0_dewPoint                       1372 non-null float64
daily_data_0_humidity                       1372 non-null float64
daily_data_0_icon                           1246 non-null object
daily_data_0_moonPhase                      1373 non-null float64
daily_data_0_ozone                  

In [37]:
columns_to_remove = [
    'daily_data_0_apparentTemperatureHigh',
    'daily_data_0_apparentTemperatureHighTime',
    'daily_data_0_apparentTemperatureLow',
    'daily_data_0_apparentTemperatureLowTime',
    'daily_data_0_apparentTemperatureMax',
    'daily_data_0_apparentTemperatureMaxTime',
    'daily_data_0_apparentTemperatureMin',
    'daily_data_0_apparentTemperatureMinTime', 
    'daily_data_0_cloudCover',
    'daily_data_0_icon', 
    'daily_data_0_ozone',
#     'daily_data_0_precipIntensity', # highly skewed with ~40% zeros
    'daily_data_0_precipIntensityMax',
    'daily_data_0_precipIntensityMaxTime',
    'daily_data_0_precipProbability',
    'daily_data_0_precipType',
    'daily_data_0_pressure', 
    'daily_data_0_summary',
    'daily_data_0_sunriseTime', # high correlation with 'daily_data_0_sunsetTime'
    'daily_data_0_temperatureHighTime', 
    'daily_data_0_temperatureLowTime',
    'daily_data_0_temperatureMax', 
    'daily_data_0_temperatureMaxTime',
    'daily_data_0_temperatureMin',
    'daily_data_0_temperatureMinTime', 
    'daily_data_0_time',
    'daily_data_0_uvIndex', # uvIndex has 1335 non-null values
    'daily_data_0_uvIndexTime', 
    'daily_data_0_visibility',
    'daily_data_0_windBearing', 
    'daily_data_0_windGust',
    'daily_data_0_windGustTime', 
    'offset', 
    'timezone',
    'daily_data_0_precipAccumulation'
#     'code',
#     'error' 
]
weather_df = weather_df.drop(columns_to_remove, axis=1)

In [38]:
weather_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1376 entries, 0 to 1375
Data columns (total 11 columns):
daily_data_0_dewPoint           1372 non-null float64
daily_data_0_humidity           1372 non-null float64
daily_data_0_moonPhase          1373 non-null float64
daily_data_0_precipIntensity    1369 non-null float64
daily_data_0_sunsetTime         1373 non-null float64
daily_data_0_temperatureHigh    1373 non-null float64
daily_data_0_temperatureLow     1371 non-null float64
daily_data_0_windSpeed          1372 non-null float64
latitude                        1376 non-null float64
longitude                       1376 non-null float64
uniqueid                        1376 non-null object
dtypes: float64(10), object(1)
memory usage: 118.4+ KB


## Rename columns

In [39]:
weather_df.columns = weather_df.columns.str.strip().str.lower().str.replace(
    'daily_data_0_', '').str.replace('(', '').str.replace(')', '')

## Drop the rows where at least one element is missing

In [40]:
weather_df.shape

(1376, 11)

In [41]:
weather_df = weather_df.dropna()
weather_df.shape

(1367, 11)

## Remove rows with erroneous 'longitude'

In [42]:
# Get names of indexes for which longitude is greater than -114 (max eastern border of California)
index_names = weather_df[(weather_df['longitude'] > -114)].index
 
# Delete these row indexes from weather_df
weather_df.drop(index_names , inplace=True)

weather_df.shape

(1365, 11)

In [390]:
profile = ProfileReport(weather_df, title='Weather Profiling Report', html={'style':{'full_width':True}})
profile.to_notebook_iframe()

# Merge wildfire and weather data frames

## Pickle data frames before merging

In [55]:
# weather_df.to_pickle('data/weather_pre_merge.pickle')
# df.to_pickle('data/pre_merge_df.pickle')

In [43]:
weather_df = pd.read_pickle('data/weather_pre_merge.pickle')
df = pd.read_pickle('data/pre_merge_df.pickle')

## Rename 'unique_id' column for the join

In [44]:
df = df.rename({'UniqueId': 'unique_id'}, axis='columns')
weather_df = weather_df.rename({'uniqueid': 'unique_id'}, axis='columns')

## Merge wildfire and weather data frames

In [45]:
wildfire_df = pd.merge(df, weather_df, how='inner', on='unique_id', sort=True).reset_index()

In [46]:
wildfire_df.shape

(1365, 27)

## Remove 'latitude' and 'longitude' columns as they are duplicated

In [47]:
wildfire_df.drop(['Latitude','Longitude'],  axis='columns', inplace=True)

## Clean column names

In [48]:
wildfire_df.columns = wildfire_df.columns.str.strip().str.lower().str.replace('(', '').str.replace(')', '')

## Convert 'started' & 'extinguished' to dates

In [49]:
wildfire_df['started'] = pd.to_datetime(wildfire_df['started'].dt.date)
wildfire_df['extinguished'] = pd.to_datetime(wildfire_df['extinguished'].dt.date)

In [50]:
wildfire_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1365 entries, 0 to 1364
Data columns (total 25 columns):
level_0             1365 non-null int64
index               1365 non-null int64
unique_id           1365 non-null object
name                1365 non-null object
location            1365 non-null object
acresburned         1365 non-null float64
counties            1365 non-null object
countyids           1365 non-null object
started             1365 non-null datetime64[ns]
extinguished        1365 non-null datetime64[ns]
calfireincident     1365 non-null object
majorincident       1365 non-null int64
datetime            1365 non-null object
durationdays        1365 non-null int64
weatherdirectory    1365 non-null object
dewpoint            1365 non-null float64
humidity            1365 non-null float64
moonphase           1365 non-null float64
precipintensity     1365 non-null float64
sunsettime          1365 non-null float64
temperaturehigh     1365 non-null float64
temperaturelo

In [51]:
columns_to_remove = [
    'level_0',
    'index',
    'location',
    'datetime',
    'counties',
    'countyids',
    'weatherdirectory'
]
wildfire_df = wildfire_df.drop(columns_to_remove, axis=1)

## Create month column

In [52]:
wildfire_df['month'] = pd.DatetimeIndex(wildfire_df['started']).month

## Remove erroneous rows

In [53]:
index_names = wildfire_df[(wildfire_df['started'] < '2013-01-01')].index
 
# Delete these row indexes from weather_df
wildfire_df.drop(index_names , inplace=True)
wildfire_df.shape

(1365, 19)

## Remove rows with zero acres burned

In [54]:
index_names = wildfire_df[(wildfire_df['acresburned'] <= 0)].index
 
# Delete these row indexes from weather_df
wildfire_df.drop(index_names , inplace=True)
wildfire_df.shape

(1341, 19)

## [Skip] Filter for Cal Fire Incidents
Data might be cleaner 

In [71]:
# wildfire_df = wildfire_df[(wildfire_df['calfireincident'] == 'true')]
# wildfire_df.shape

(1060, 19)

## [Skip] Remove rows with duration > 52 days
https://mashable.com/article/wildfire-burn-how-long-climate-change/

In [536]:
# index_names = wildfire_df[(wildfire_df['durationdays'] > 60) | (wildfire_df['durationdays'] <= 1)].index
 
# # Delete these row indexes from weather_df
# wildfire_df.drop(index_names , inplace=True)
# wildfire_df.shape

# Final Exploratory Data Analysis

## Pickle data frame

In [88]:
# wildfire_df.to_pickle('data/wildfire_pre_eda.pickle')

In [56]:
# wildfire_df = pd.read_pickle('data/wildfire_pre_eda.pickle')

## Profile report for 'wildfire_df'

In [57]:
profile = ProfileReport(wildfire_df, title='Wildfire Profiling Report', html={'style':{'full_width':True}})
profile.to_notebook_iframe()

# [Canceled Items]

## [Canceled] Parse Data with Selenium & BeautifulSoup

In [ ]:
# import os
# from selenium import webdriver
# from selenium.webdriver.common.keys import Keys
# import time

# chromedriver = "/Applications/chromedriver" # path to the chromedriver executable
# os.environ["webdriver.chrome.driver"] = chromedriver

In [ ]:
# url = 'https://www.fire.ca.gov/incidents/2019/' 

# driver = webdriver.Chrome(chromedriver)
# driver.get(url)
# time.sleep(3)

In [ ]:
# element = driver.find_element_by_tag_name('body')

In [ ]:
# for _ in range(5):
#     element.send_keys(Keys.SPACE)

In [ ]:
# html = driver.execute_script("return document.body.innerHTML")

In [ ]:
# soup = BeautifulSoup(html, 'html.parser')

In [ ]:
# stuff = soup.find_all('div', {'class':'responsive-table-row'})

In [ ]:
# [entry.text.strip() for entry in stuff]

In [ ]:
# for row in stuff:
#     row = row.text.strip()
#     print(row)    

In [ ]:
# driver.quit()